In [1]:
import os
import re
import time
import math
import torch
import random
import pickle
import os.path
import torchtext
import matplotlib
import numpy as np
import pandas as pd
import torch.nn as nn
import sentencepiece as spm


from glob import glob
from torch import optim
from itertools import cycle
from torchtext import vocab
from konlpy.tag import Mecab
from torchinfo import summary
from torch.nn import Transformer
from torch.utils.data import DataLoader
#from torchaudio.models import Conformer
from timeit import default_timer as timer
from soyspacing.countbase import CountSpace
from torch.nn.utils.rnn import pad_sequence
from torchmetrics.functional import word_error_rate
from nltk.translate.bleu_score import sentence_bleu
from torchtext.vocab import build_vocab_from_iterator


mecab = Mecab()

In [2]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

torch.manual_seed(777)

if device == 'cuda':
    torch.cuda.manual_seed_all(777)


In [3]:
os.chdir("/data/kmkim/chatbot_data_model/dental_5/5_data/prepro") ## .pkl 데이터가 있는 폴더로 이동
with open('patient_5_patient_data.pkl', 'rb') as f: ## 전처리한 환자 .pkl 데이터 로드
    data_load = pickle.load(f)

In [5]:
valid_load = data_load

In [7]:
valid_load

[['선생님, 평소에 치아 말고 치료 받은 다른 부위가 있으실까요?', '피부과 치료를 받고 있어요.'],
 ['혹시 아프신 곳이 어딘가요?', '오른쪽 위 아래 송곳니 부분이 아파요.'],
 ['환자분, 안녕하세요 오늘 날씨가 정말 좋네요.', '네 그러네요.'],
 ['선생님, 아프신 곳이 어디일까요?', '오른쪽 위 아래 송곳니 부분이 아파요.'],
 ['평소에 치과에서 검사 받으실때 따로 마취한 적 있으세요?', '아뇨 없습니다.'],
 ['선생님, 따로 처방받은 약은 없으시고요?', '영양제 먹어요.'],
 ['성함 말씀해 주세요.', '제 이름은 박영희입니다.'],
 ['전기로 치아 신경 검사를 해보곘습니다', '네 알겠습니다.'],
 ['혹시 주에 음주를 얼마나 자주 하세요?', '두 달에 서너 번 마셔요.'],
 ['선생님, 그러면 방사선 사진을 찍어 염증을 확인하겠습니다.', '네 알겠습니다.'],
 ['치아 이외에 아프신 곳 있으신가요?', '피부과 치료를 받고 있어요.'],
 ['아픔의 정도를 점수로 하면 몇 점일까요?', '5점 정도 같아요.'],
 ['선생님, 다시 한번 확인 할게요 성함 좀 말씀해 주실래요?', '제 이름은 박영희입니다.'],
 ['다시 한번 확일 할게요 21세 입니까?', '네, 맞습니다.'],
 ['현재 복용하고 계신 약이 따로 있을까요?', '영양제 먹어요.'],
 ['선생님, 지금부터 이쪽 치아를 건드려 보겠습니다.', '네 알겠습니다.'],
 ['아프시다는 곳을 흔들어 보겠습니다.', '네 알겠습니다.'],
 ['혹시 아프신 부분이 어딘가요?', '오른쪽 위 아래 송곳니 부분이 아파요.'],
 ['치아 뿌리 부분 염증 유무 확인을 위해 방사선 사진을 찍겠습니다.', '네 알겠습니다.'],
 ['어디 치아가 아파서 진찰받으러 오셨나요?', '오른쪽 위 아래 송곳니 부분이 아파요.'],
 ['선생님, 주기적으로 복용하시는 약이 있을까요?', '영양제 먹어요.'],
 ['주기적으로 드시고 계신 약이 있으세요?', '

In [8]:
length_list = []

for q in data_load:
    length_list.append(len(q[0]))

max_length = max(length_list)

In [35]:

os.chdir("/data/kmkim/chatbot_data_model/dental_5/5_data/prepro") ## 'FastText_' 시작하는 파일이 있는 위치로 이동

def load_embedding():
    que_emb= torchtext.vocab.Vectors('FastText_patient_patient_data_5') ## 'FastText_' 로 시작하는 각 환자에 대한 파일 불러오기
    
    
    que_vocab = torchtext.vocab.vocab(que_emb.stoi, min_freq= 0, specials = ["<unk>", "<pad>", "<sos>", "<eos>"])

    
    vector_dic = {'que': que_emb} 
    
    vocab_dic = {'que': que_vocab}
    

    a = torch.zeros(4,256, requires_grad = True)                                
    que_emb.vectors = torch.cat([a, que_emb.vectors], dim=0)      
    que_emb.stoi = dict(zip(que_emb.stoi.keys(), map(lambda x:x[1]+4, que_emb.stoi.items()))) 
    for i, j in enumerate(["<unk>", "<pad>", "<sos>", "<eos>"]):
        que_emb.stoi[j] = i                 
    que_vocab.set_default_index(0)                    
    
    return que_vocab, que_emb

In [36]:
pre_vocab, pre_vector = load_embedding()

In [39]:
def for_yield_vocab_tokenizer(sentence):
    for i in sentence:
        tokens1 = mecab.morphs(i[0]) 
        tokens2 = mecab.morphs(i[1])
        total_tokens = tokens1 + tokens2
        yield total_tokens
        
def tokenizer(sentence):
    return mecab.morphs(sentence)

In [40]:
from typing import Optional, Tuple


__all__ = ["Conformer"]




class _ConvolutionModule(torch.nn.Module):
    r"""Conformer convolution module.

    Args:
        input_dim (int): input dimension.
        num_channels (int): number of depthwise convolution layer input channels.
        depthwise_kernel_size (int): kernel size of depthwise convolution layer.
        dropout (float, optional): dropout probability. (Default: 0.0)
        bias (bool, optional): indicates whether to add bias term to each convolution layer. (Default: ``False``)
        use_group_norm (bool, optional): use GroupNorm rather than BatchNorm. (Default: ``False``)
    """

    def __init__(
        self,
        input_dim: int,
        num_channels: int,
        depthwise_kernel_size: int,
        dropout: float = 0.0,
        bias: bool = False,
        use_group_norm: bool = False,
    ) -> None:
        super().__init__()
        if (depthwise_kernel_size - 1) % 2 != 0:
            raise ValueError("depthwise_kernel_size must be odd to achieve 'SAME' padding.")
        self.layer_norm = torch.nn.LayerNorm(input_dim)
        self.sequential = torch.nn.Sequential(
            torch.nn.Conv1d(
                input_dim,
                2 * num_channels,
                1,
                stride=1,
                padding=0,
                bias=bias,
            ),
            torch.nn.GLU(dim=1),
            torch.nn.Conv1d(
                num_channels,
                num_channels,
                depthwise_kernel_size,
                stride=1,
                padding=(depthwise_kernel_size - 1) // 2,
                groups=num_channels,
                bias=bias,
            ),
            torch.nn.GroupNorm(num_groups=1, num_channels=num_channels)
            if use_group_norm
            else torch.nn.BatchNorm1d(num_channels),
            torch.nn.SiLU(),
            torch.nn.Conv1d(
                num_channels,
                input_dim,
                kernel_size=1,
                stride=1,
                padding=0,
                bias=bias,
            ),
            torch.nn.Dropout(dropout),
        )

    def forward(self, input: torch.Tensor) -> torch.Tensor:
        r"""
        Args:
            input (torch.Tensor): with shape `(B, T, D)`.

        Returns:
            torch.Tensor: output, with shape `(B, T, D)`.
        """
        x = self.layer_norm(input)
        x = x.transpose(1, 2)
        x = self.sequential(x)
        return x.transpose(1, 2)


class _FeedForwardModule(torch.nn.Module):
    r"""Positionwise feed forward layer.

    Args:
        input_dim (int): input dimension.
        hidden_dim (int): hidden dimension.
        dropout (float, optional): dropout probability. (Default: 0.0)
    """

    def __init__(self, input_dim: int, hidden_dim: int, dropout: float = 0.0) -> None:
        super().__init__()
        self.sequential = torch.nn.Sequential(
            torch.nn.LayerNorm(input_dim),
            torch.nn.Linear(input_dim, hidden_dim, bias=True),
            torch.nn.SiLU(),
            torch.nn.Dropout(dropout),
            torch.nn.Linear(hidden_dim, input_dim, bias=True),
            torch.nn.Dropout(dropout),
        )

    def forward(self, input: torch.Tensor) -> torch.Tensor:
        r"""
        Args:
            input (torch.Tensor): with shape `(*, D)`.

        Returns:
            torch.Tensor: output, with shape `(*, D)`.
        """
        return self.sequential(input)


class ConformerLayer(torch.nn.Module):
    r"""Conformer layer that constitutes Conformer.

    Args:
        input_dim (int): input dimension.
        ffn_dim (int): hidden layer dimension of feedforward network.
        num_attention_heads (int): number of attention heads.
        depthwise_conv_kernel_size (int): kernel size of depthwise convolution layer.
        dropout (float, optional): dropout probability. (Default: 0.0)
        use_group_norm (bool, optional): use ``GroupNorm`` rather than ``BatchNorm1d``
            in the convolution module. (Default: ``False``)
        convolution_first (bool, optional): apply the convolution module ahead of
            the attention module. (Default: ``False``)
    """

    def __init__(
        self,
        input_dim: int,
        ffn_dim: int,
        num_attention_heads: int,
        depthwise_conv_kernel_size: int,
        dropout: float = 0.0,
        use_group_norm: bool = False,
        convolution_first: bool = False,
    ) -> None:
        super().__init__()

        self.ffn1 = _FeedForwardModule(input_dim, ffn_dim, dropout=dropout)

        self.self_attn_layer_norm = torch.nn.LayerNorm(input_dim)
        self.self_attn = torch.nn.MultiheadAttention(input_dim, num_attention_heads, dropout=dropout)
        self.self_attn_dropout = torch.nn.Dropout(dropout)

        self.conv_module = _ConvolutionModule(
            input_dim=input_dim,
            num_channels=input_dim,
            depthwise_kernel_size=depthwise_conv_kernel_size,
            dropout=dropout,
            bias=True,
            use_group_norm=use_group_norm,
        )

        self.ffn2 = _FeedForwardModule(input_dim, ffn_dim, dropout=dropout)
        self.final_layer_norm = torch.nn.LayerNorm(input_dim)
        self.convolution_first = convolution_first

    def _apply_convolution(self, input: torch.Tensor) -> torch.Tensor:
        residual = input
        input = input.transpose(0, 1)
        input = self.conv_module(input)
        input = input.transpose(0, 1)
        input = residual + input
        return input

    def forward(self, input: torch.Tensor, key_padding_mask: Optional[torch.Tensor]) -> torch.Tensor:
        r"""
        Args:
            input (torch.Tensor): input, with shape `(T, B, D)`.
            key_padding_mask (torch.Tensor or None): key padding mask to use in self attention layer.

        Returns:
            torch.Tensor: output, with shape `(T, B, D)`.
        """
        residual = input
        x = self.ffn1(input)
        x = x * 0.5 + residual

        if self.convolution_first:
            x = self._apply_convolution(x)

        residual = x
        x = self.self_attn_layer_norm(x)
        x, _ = self.self_attn(
            query=x,
            key=x,
            value=x,
            key_padding_mask=key_padding_mask,
            need_weights=False,
        )
        x = self.self_attn_dropout(x)
        x = x + residual

        if not self.convolution_first:
            x = self._apply_convolution(x)

        residual = x
        x = self.ffn2(x)
        x = x * 0.5 + residual

        x = self.final_layer_norm(x)
        return x


class Conformer(torch.nn.Module):
    r"""Conformer architecture introduced in
    *Conformer: Convolution-augmented Transformer for Speech Recognition*
    :cite:`gulati2020conformer`.

    Args:
        input_dim (int): input dimension.
        num_heads (int): number of attention heads in each Conformer layer.
        ffn_dim (int): hidden layer dimension of feedforward networks.
        num_layers (int): number of Conformer layers to instantiate.
        depthwise_conv_kernel_size (int): kernel size of each Conformer layer's depthwise convolution layer.
        dropout (float, optional): dropout probability. (Default: 0.0)
        use_group_norm (bool, optional): use ``GroupNorm`` rather than ``BatchNorm1d``
            in the convolution module. (Default: ``False``)
        convolution_first (bool, optional): apply the convolution module ahead of
            the attention module. (Default: ``False``)

    Examples:
        >>> conformer = Conformer(
        >>>     input_dim=80,
        >>>     num_heads=4,
        >>>     ffn_dim=128,
        >>>     num_layers=4,
        >>>     depthwise_conv_kernel_size=31,
        >>> )
        >>> lengths = torch.randint(1, 400, (10,))  # (batch,)
        >>> input = torch.rand(10, int(lengths.max()), input_dim)  # (batch, num_frames, input_dim)
        >>> output = conformer(input, lengths)
    """

    def __init__(
        self,
        input_dim: int,
        num_heads: int,
        ffn_dim: int,
        num_layers: int,
        depthwise_conv_kernel_size: int,
        dropout: float = 0.0,
        use_group_norm: bool = False,
        convolution_first: bool = False,
    ):
        super().__init__()

        self.conformer_layers = torch.nn.ModuleList(
            [
                ConformerLayer(
                    input_dim,
                    ffn_dim,
                    num_heads,
                    depthwise_conv_kernel_size,
                    dropout=dropout,
                    use_group_norm=use_group_norm,
                    convolution_first=convolution_first,
                )
                for _ in range(num_layers)
            ]
        )
    def _lengths_to_padding_mask(self, lengths: torch.Tensor) -> torch.Tensor:
        batch_size = lengths.shape[0]
        max_length = int(torch.max(lengths).item())
        padding_mask = torch.arange(max_length, device=lengths.device, dtype=lengths.dtype).expand(
            batch_size, max_length
        ) >= lengths.unsqueeze(1)
        return padding_mask
    

    def forward(self, input: torch.Tensor, lengths: torch.Tensor) -> Tuple[torch.Tensor, torch.Tensor]:
        r"""
        Args:
            input (torch.Tensor): with shape `(B, T, input_dim)`.
            lengths (torch.Tensor): with shape `(B,)` and i-th element representing
                number of valid frames for i-th batch element in ``input``.

        Returns:
            (torch.Tensor, torch.Tensor)
                torch.Tensor
                    output frames, with shape `(B, T, input_dim)`
                torch.Tensor
                    output lengths, with shape `(B,)` and i-th element representing
                    number of valid frames for i-th batch element in output frames.
        """
        encoder_padding_mask = self._lengths_to_padding_mask(lengths)

        x = input.transpose(0, 1)
        for layer in self.conformer_layers:
            x = layer(x, encoder_padding_mask)
        return x.transpose(0, 1), lengths, encoder_padding_mask 

In [41]:
## Transformer에 적용되는 함수와 모델


class PositionalEncoding(nn.Module):
    def __init__(self, emb_size, max_len, dropout ):
        super(PositionalEncoding, self).__init__()
        
        den = torch.exp(- torch.arange(0, emb_size, 2) * math.log(10000) / emb_size) ## shape = (1,256)
        pos = torch.arange(0, max_len).reshape(max_len, 1) ## shape (maxlen, 1)
        
        pos_embedding = torch.zeros((max_len, emb_size))
        pos_embedding[:, 0::2] = torch.sin(pos * den)
        pos_embedding[:, 1::2] = torch.cos(pos * den)
        pos_embedding = pos_embedding.unsqueeze(-2)
        
        self.dropout = nn.Dropout(dropout)
        self.register_buffer('pos_embedding', pos_embedding) ## opimizer가 업데이트 하지 않음, 그러나 값은 존재, GPU연산 가능, 업데이트 하고싶지 않은 층
        
    def forward(self, token_embedding):
        return self.dropout(token_embedding + self.pos_embedding[:token_embedding.size(0), :])
    

class TokenEmbedding(nn.Module):
    def __init__(self, vocab_size, emb_size):
        super(TokenEmbedding,self).__init__()
        self.embedding = nn.Embedding(vocab_size, emb_size, padding_idx = 1) ## 단어사전 
        self.emb_size = emb_size
    
    def forward(self, tokens):
        return self.embedding(tokens.long()) * math.sqrt(self.emb_size)
    
    
class pre_TokenEmbedding(nn.Module): ## pretrain_word embedding
    def __init__(self, vocab, emb_size):
        super(pre_TokenEmbedding,self).__init__()
        self.embedding = nn.Embedding.from_pretrained(vocab.vectors, padding_idx=1, freeze= False)
        self.emb_size = emb_size
    def forward(self, tokens):
        return self.embedding(tokens.long()) * math.sqrt(self.emb_size)
    

class Seq2SeqTransformer(nn.Module):
    def __init__(self, 
                 num_encoder_layers,
                 num_decoder_layers,
                 emb_size, 
                 nhead,
                 src_vocab_size,
                 tgt_vocab_size,
                 max_len,
                 dim_feedforward = 512, 
                 dropout = 0.4,
                pretrain = False):
        
        self.pretrain = pretrain
        super(Seq2SeqTransformer,self).__init__()
        

        self.conformer = Conformer(input_dim = emb_size,
                                   num_heads=nhead,
                                   ffn_dim = dim_feedforward,
                                   num_layers = num_encoder_layers,
                                   depthwise_conv_kernel_size = 31, 
                                   dropout = dropout)
        
        self.decoder_layer = nn.TransformerDecoderLayer(d_model = emb_size,
                                                        dim_feedforward = dim_feedforward,
                                                        dropout= dropout,
                                                       nhead = nhead,
                                                       device = device)
        
        self.transformer_decoder = nn.TransformerDecoder(self.decoder_layer, num_layers=num_decoder_layers)
        
        self.generator = nn.Linear(emb_size, tgt_vocab_size)
        
        if pretrain == True:
            self.src_tok_emb = pre_TokenEmbedding(pre_vector, emb_size)
            self.tgt_tok_emb = pre_TokenEmbedding(pre_vector, emb_size)

        else:
            self.src_tok_emb = TokenEmbedding(src_vocab_size, emb_size) 
            self.tgt_tok_emb = TokenEmbedding(tgt_vocab_size, emb_size)

            
        self.positional_encoding = PositionalEncoding(emb_size, max_len, dropout = dropout)

    def forward(self, src, tgt, tgt_mask, tgt_padding_mask, lengths):

        src_emb = self.positional_encoding(self.src_tok_emb(src)) # seq, batch, dim
        src_emb = src_emb.permute(1,0,2) ## batch, seq, dim
        tgt_emb = self.positional_encoding(self.tgt_tok_emb(tgt))
        memory = self.conformer(src_emb, lengths) ## batch, seq, dim
        encoder_padding_mask = memory[2]
        memory = memory[0].permute(1,0,2) ## seq, batch, dim
        outs = self.transformer_decoder(tgt_emb, memory, tgt_mask = tgt_mask, 
                                        tgt_key_padding_mask = tgt_padding_mask, 
                                        memory_key_padding_mask = encoder_padding_mask)
        return self.generator(outs)
        
    def encode(self, src, lengths):
        return self.conformer(self.positional_encoding(self.src_tok_emb(src)).permute(1,0,2), lengths)
    
    def decoder(self,tgt, memory, tgt_mask):
        return self.transformer_decoder(self.positional_encoding(self.tgt_tok_emb(tgt)),
                                       memory, tgt_mask)


In [42]:
def generate_square_subsequent_mask(sz):
    mask = (torch.triu(torch.ones((sz,sz), device = device ))== 1).T  
    mask = mask.float().masked_fill(mask==0, float('-inf')).masked_fill(mask == 1, float(0.0)) 
    return mask

def create_mask(src,tgt):
    src_seq_len = src.shape[0]   ## sequence_length
    tgt_seq_len = tgt.shape[0]   ## sequence_length
    
    tgt_mask = generate_square_subsequent_mask(tgt_seq_len) ## 디코더에서 셀프 어텐션 할때 그 뒤를 못보게 마스킹
    src_mask = torch.zeros((src_seq_len, src_seq_len), device = device).type(torch.bool)
    
    src_padding_mask = (src == 1).T 
    tgt_padding_mask = (tgt == 1).T
    return src_mask, tgt_mask, src_padding_mask, tgt_padding_mask

In [43]:
SRC_VOCAB_SIZE = len(pre_vocab) 
TGT_VOCAB_SIZE = len(pre_vocab) 
EMB_SIZE = 256
NHEAD = 8
FFN_HID_DIM = 512
BATCH_SIZE = 128
NUM_ENCODER_LAYERS = 4 ## 3  
NUM_DECODER_LAYERS = 4 ## 3


In [44]:
transformer = Seq2SeqTransformer(NUM_ENCODER_LAYERS, NUM_DECODER_LAYERS, EMB_SIZE, NHEAD, SRC_VOCAB_SIZE, TGT_VOCAB_SIZE, max_length, FFN_HID_DIM,
                                 pretrain = True)

for p in transformer.parameters():
    if p.dim() > 1:
        nn.init.xavier_uniform_(p)

transformer = transformer.to(device)

loss_fn = torch.nn.CrossEntropyLoss(ignore_index = 1)

optimizer = torch.optim.Adam(transformer.parameters(), lr = 5e-4, betas = (0.9,0.98), eps = 1e-9) ## lr = 4e-4 

In [45]:
def sequential_transforms(*transforms):
    def func(txt_input):
        for transform in transforms:
            txt_input = transform(txt_input)
        return txt_input
    return func

def tensor_transform(token_ids):
    return torch.cat((torch.tensor([2]),
                     torch.tensor(token_ids),
                     torch.tensor([3])))
text_transform = {}


text_transform['kor'] = sequential_transforms(tokenizer, pre_vocab, tensor_transform) 


In [46]:
def collate_fn(batch):
    src_batch, tgt_batch, lengths = [], [], []
    for src_sample, tgt_sample in batch:
        src_batch.append(text_transform['kor'](src_sample))
        tgt_batch.append(text_transform['kor'](tgt_sample))
    for i in src_batch:
        lengths.append(len(i))
    
    src_batch = pad_sequence(src_batch, padding_value = 1.0)
    tgt_batch = pad_sequence(tgt_batch, padding_value = 1.0)
    lengths = torch.LongTensor(lengths)
    return src_batch, tgt_batch, lengths

In [49]:
train_loader = DataLoader(data_load, batch_size = BATCH_SIZE, shuffle = True, collate_fn = collate_fn, drop_last = True ,num_workers = 2)
valid_loader = DataLoader(valid_load, batch_size =BATCH_SIZE, shuffle = True, collate_fn= collate_fn, drop_last = True, num_workers = 2)


In [50]:
def train_epoch(model, optimizer, train_loader, valid_loader):
    '''
        Args:
            model (Module)
            optimizer (Optimizer)
            train_loader (Dataloader)
            valid_loader (Dataloader)
    '''

    model.train()
    losses = 0
    val_losses = 0

    for src,tgt, lengths in train_loader:
        src = src.to(device)
        tgt = tgt.to(device)
        lengths= lengths.to(device)
        
        tgt_input = tgt[:-1, :]
        
        src_mask, tgt_mask, src_padding_mask, tgt_padding_mask = create_mask(src, tgt_input)
        
        logits = model(src, tgt_input, tgt_mask, tgt_padding_mask,lengths)
        
        optimizer.zero_grad()
        
        tgt_out = tgt[1:, :]
        
        loss = loss_fn(logits.reshape(-1, logits.shape[-1]), tgt_out.reshape(-1))
        loss.backward()
        
        optimizer.step()
        losses += loss.item()
    
    for src, tgt, lengths in valid_loader:
        model.eval()
        with torch.no_grad():
            src = src.to(device)
            tgt = tgt.to(device)
            lengths = lengths.to(device) 

            tgt_input = tgt[:-1, :]

            src_mask, tgt_mask, src_padding_mask, tgt_padding_mask = create_mask(src, tgt_input)

            logits = model(src, tgt_input, tgt_mask, tgt_padding_mask,lengths)

            tgt_out = tgt[1:, :]

            loss = loss_fn(logits.reshape(-1, logits.shape[-1]), tgt_out.reshape(-1))

            val_losses += loss.item()

    
    return losses / len(train_loader) , val_losses / len(valid_loader)


In [51]:
def new_greedy_decode(model, lengths, src, src_mask, max_len, start_symbol ):

    memory = model.encode(src, lengths)[0].permute(1,0,2)
    ys = torch.ones(1,src.size(1)).fill_(start_symbol).type(torch.long).to(device)
    for i in range(max_len):
        tgt_mask = (generate_square_subsequent_mask(ys.size(0)))
        out = model.decoder(ys, memory, tgt_mask)
        out = out.transpose(0,1) # (sequence ,batch, hidden)  -> (batch,sequence ,hidden)
        prob = model.generator(out[:, -1]) ## 마지막 단어
        _, next_word = torch.max(prob, dim = 1)
        next_word = next_word.unsqueeze(0)
        ys = torch.cat([ys, next_word], dim = 0)
    return ys

In [52]:
def translate_bleu(model,testset):
    total_bleu = 0
    total_wer = 0
    acc = 0
    model.eval()
    with torch.no_grad():
        for loader_idx ,(src, tgt, lengths) in enumerate(testset):
            src = src.to(device)
            tgt = tgt.to(device)
            lengths = lengths.to(device)
            target_length = tgt.size(0)
            num_tokens = src.shape[0] 
            
            src_mask = (torch.zeros(num_tokens, num_tokens)).type(torch.bool) 
            tgt_tokens = new_greedy_decode(model, lengths, src, src_mask, max_len = num_tokens, start_symbol=2) #.flatten()
 
            decoded_words = [] ## 예측 문장들을 담는 list
                                                        ## 예측 결과
            for batch_idx in range(src.size(1)):        ## 배치의 각 문장마다 돌면서 <eos> 토큰을 만나면 문장을 끊도록
                a = tgt_tokens[:, batch_idx]             ## idx 번째 배치의 문장 가져오기, a
                subwords = []                            ## 배치의 문장을 담을 list
                for sent_idx, k in enumerate(a):     
                    if a[sent_idx] == 3:                
                        subwords.append("<eos>")
                        subwords = (" ".join(subwords)).replace("<sos>", "").replace("<eos>","").replace("<pad>", "")
                        decoded_words.append(subwords)
                        break
                    else:
                        subwords.append(pre_vocab.lookup_token(a[sent_idx])) ## index to word 
                        if len(subwords) == (len(tgt_tokens)):
                            subwords.append("<eos>")
                            subwords = (" ".join(subwords)).replace("<sos>", "").replace("<eos>","").replace("<pad>", "")
                            decoded_words.append(subwords)
                            break 
                            

            for pred_idx in range(src.size(1)): ## 각 시퀀스를 돌면서 계산
                predict_equ = decoded_words[pred_idx]
                real_equ = (" ".join(pre_vocab.lookup_tokens(tgt.T.tolist()[pred_idx]))).replace("<sos>", "").replace("<eos>","").replace("<pad>", "")
    
                
                decoded_words[pred_idx] = mecab.morphs(decoded_words[pred_idx])
                decoded_words[pred_idx].extend(["<eos>"])
                
                real = mecab.morphs(real_equ)
                real.extend(["<eos>"])
                

                wer = word_error_rate(real, decoded_words[pred_idx])
                bleu = sentence_bleu([real], decoded_words[pred_idx],smoothing_function =None )
                total_bleu += bleu   
                total_wer += wer.item()    
                
        
    return total_bleu / len(testset.dataset), total_wer/ len(testset.dataset)

In [53]:
os.chdir('/data/kmkim/chatbot_data_model/dental_5/dental_conformer_model_losses') ## 모델 학습 loss 저장 위치
t = open('Conformer_patient5_train_losses','w') ## 모델 학습 loss 저장 파일,,  성능 지표 필요 없으면 지워도 무방
b = open('Conformer_patient5_bleu_scores','w')  ## 모델 학습 BLEU 점수 저장 파일
v = open('Conformer_patient5_valid_losses','w') ## 모델 학습 valid loss 점수 저장 파일
a = open('Conformer_patient5_accuracy','w')     ## 모델 학습 WER 점수 저장 파일
t.close()
b.close()
v.close()
a.close()

In [54]:
import os
NUM_EPOCHS = 300 ## 50
best_val_loss = None
before_loss = 999999
count = 0
'''
train_losses = []
val_losses = []
bleu_scores = []
acc_list = []
'''
for epoch in range(0, 7):
    os.chdir('/data/kmkim/chatbot_data_model/dental_5/dental_conformer_model_losses') ## 모델 학습 loss 저장 위치
    t = open('Conformer_patient5_train_losses','a') ## 모델 학습 loss 갱신값 저장
    b = open('Conformer_patient5_bleu_scores','a')
    v = open('Conformer_patient5_valid_losses','a')
    a = open('Conformer_patient5_accuracy','a')
    try:
        start_time = timer()
        train_loss, val_loss= train_epoch(transformer, optimizer, train_loader, valid_loader)
        end_time = timer()
        bleu_score, wer = translate_bleu(transformer, valid_loader)
        valid_end_time = timer()
        
        
        t.write(str(train_loss) + '\n')
        b.write(str(bleu_score) + '\n')
        v.write(str(val_loss) + '\n')
        a.write(str(wer) + '\n')
    
    finally:
        
        t.close()
        b.close()
        v.close()
        a.close()
            
        
    print(f"EPOCH : {epoch}, Train Loss : {train_loss}, Val Loss: {val_loss}, Val_Bleu_Score :{bleu_score}, Val_acc: {wer} \
train_time : {(end_time - start_time):.3f}s, valid_time :{(valid_end_time -end_time)}s")
    
    before_loss = val_loss
    
    if not best_val_loss or val_loss < best_val_loss:
        os.chdir('/data/kmkim/chatbot_data_model/dental_5') 
        if not os.path.isdir("conformer_save"): ## 모델 저장 폴더 생성
            os.makedirs("conformer_save")
        
        torch.save(transformer.state_dict(), 'conformer_save/Conformer_patient5.pt')  ## 모델 저장
        print("model saved")
        best_val_loss = val_loss
        count = 0
        
    else:
        count += 1
        if count == 10:
            print("overfitting")
            break

/opt/conda/lib/python3.8/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/opt/conda/lib/python3.8/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/opt/conda/lib/python3.8/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg

EPOCH : 0, Train Loss : 1.8028731383383274, Val Loss: 0.06392196679135433, Val_Bleu_Score :0.9094848449389795, Val_acc: 0.06600453753417033 train_time : 15.839s, valid_time :30.00978187902365s
model saved
EPOCH : 1, Train Loss : 0.07935025513398687, Val Loss: 0.0004242999377704502, Val_Bleu_Score :0.9993668882557771, Val_acc: 0.00010551862403714256 train_time : 10.813s, valid_time :31.951602214947343s
model saved
EPOCH : 2, Train Loss : 0.01013163461135952, Val Loss: 0.0003687346826720042, Val_Bleu_Score :0.9990503323836657, Val_acc: 0.0003869016172765893 train_time : 11.636s, valid_time :31.003803693922237s
model saved
EPOCH : 3, Train Loss : 0.0055108157181608915, Val Loss: 8.002143757137773e-06, Val_Bleu_Score :0.9994724068798143, Val_acc: 0.0 train_time : 11.749s, valid_time :33.73523227905389s
model saved
EPOCH : 4, Train Loss : 0.0028663158316064525, Val Loss: 5.179165539728372e-06, Val_Bleu_Score :0.9994724068798143, Val_acc: 0.0 train_time : 12.414s, valid_time :30.821465060929

In [ ]:
### 학습 완료 후 모델 검증

In [59]:
os.chdir('../conformer_save') 

In [60]:
transformer_T = Seq2SeqTransformer(NUM_ENCODER_LAYERS, NUM_DECODER_LAYERS, EMB_SIZE, NHEAD, SRC_VOCAB_SIZE, TGT_VOCAB_SIZE, max_length, FFN_HID_DIM,
                                 pretrain = True)
transformer_T = transformer_T.to(device)
transformer_T.load_state_dict(torch.load('/data/kmkim/chatbot_data_model/dental_5/conformer_save/Conformer_patient5.pt')) # 학습 시킨 모델 로드

<All keys matched successfully>

In [73]:
def new_new_greedy_decode(model, lengths, src, max_len, start_symbol):

    memory = model.encode(src, lengths)[0].permute(1,0,2)
    ys = torch.ones(1,src.size(1)).fill_(start_symbol).type(torch.long).to(device)
    for i in range(max_len):
        tgt_mask = (generate_square_subsequent_mask(ys.size(0)))
        out = model.decoder(ys, memory, tgt_mask)
        out = out.transpose(0,1) # (sequence ,batch, hidden)  -> (batch,sequence ,hidden)
        prob = model.generator(out[:, -1]) ## 마지막 단어
        _, next_word = torch.max(prob, dim = 1)
        if next_word == 3:
            break
        next_word = next_word.unsqueeze(0)
        ys = torch.cat([ys, next_word], dim = 0)
    return ys

In [74]:
def translate(model, src_sentence):
    model.eval()
    src = text_transform['kor'](src_sentence).view(-1, 1)
    src = src.to(device)
    num_tokens = src.shape[0]
    num_tokens = torch.tensor([num_tokens]).to(device)
    tgt_tokens = new_new_greedy_decode(
        model, num_tokens,  src, max_len=num_tokens + 4, start_symbol=2).flatten()
    return (" ".join(pre_vocab.lookup_tokens(tgt_tokens.tolist()))).replace("<sos>", "").replace("<eos>","").replace("<pad>", "") 

In [66]:
def chatbot_bleu(model,testset):
    total_bleu = 0
    total_wer = 0
    acc = 0
    model.eval()
    with torch.no_grad():
        for loader_idx ,(src, tgt, lengths) in enumerate(testset):
            src = src.to(device)
            tgt = tgt.to(device)
            lengths = lengths.to(device)
            target_length = tgt.size(0)
            num_tokens = src.shape[0] ## sequnce_length
            
            src_mask = (torch.zeros(num_tokens, num_tokens)).type(torch.bool) 
            tgt_tokens = new_greedy_decode(model, lengths, src, src_mask, max_len = num_tokens, start_symbol=2) #.flatten()
 
            decoded_words = [] ## 예측 문장들을 담는 list
                                                        ## 예측 결과
            for batch_idx in range(src.size(1)):        ## 배치의 각 문장마다 돌면서 <eos> 토큰을 만나면 문장을 끊도록
                a = tgt_tokens[:, batch_idx]             ## idx 번째 배치의 문장 가져오기, a
                subwords = []                            ## 배치의 문장을 담을 list
                for sent_idx, k in enumerate(a):     
                    if a[sent_idx] == 3:                
                        subwords.append("<eos>")
                        subwords = (" ".join(subwords)).replace("<sos>", "").replace("<eos>","").replace("<pad>", "")
                        decoded_words.append(subwords)
                        break
                    else:
                        subwords.append(pre_vocab.lookup_token(a[sent_idx])) ## index to word 
                        if len(subwords) == (len(tgt_tokens)):
                            subwords.append("<eos>")
                            subwords = (" ".join(subwords)).replace("<sos>", "").replace("<eos>","").replace("<pad>", "")
                            decoded_words.append(subwords)
                            break 
                            
            #predict_tgt = " ".join(equ_vocab.lookup_tokens(list(tgt_tokens.cpu().numpy()))).replace("<sos>", "").replace("<eos>", "")            

            for pred_idx in range(src.size(1)): ## 각 시퀀스를 돌면서 계산
                predict_equ = decoded_words[pred_idx]
                real_equ = (" ".join(pre_vocab.lookup_tokens(tgt.T.tolist()[pred_idx]))).replace("<sos>", "").replace("<eos>","").replace("<pad>", "")
    
                
                decoded_words[pred_idx] = mecab.morphs(decoded_words[pred_idx])
                decoded_words[pred_idx].extend(["<eos>"])
                
                real = mecab.morphs(real_equ)
                real.extend(["<eos>"])
                print(pred_idx)
                print("question =",(' '.join(pre_vocab.lookup_tokens(src.T.tolist()[pred_idx]))).replace("<pad>", "").replace("<eos>",""))
                print('real =', ' '.join((real)))
                print('predicted=',  ' '.join(decoded_words[pred_idx]))
                print("-----------------------------------------")
                wer = word_error_rate(real, decoded_words[pred_idx])
                bleu = sentence_bleu([real], decoded_words[pred_idx],smoothing_function =None )
                total_bleu += bleu   ## 배치의 bleu score 저장 나중에 총 배치 개수로 나눠 줘야함
                total_wer += wer
                
        
    return total_bleu / len(testset.dataset), total_wer/ len(testset.dataset)

In [67]:
bleu_score, wer = chatbot_bleu(transformer_T, valid_loader)
print(bleu_score, wer)

0
question = <sos> 혹시 치과 말 고 다른 병원 에서 치료 받 은 적 이 있 으신 가요 ?            
real = 피부과 치료 를 받 고 있 어요 . <eos>
predicted= 피부과 치료 를 받 고 있 어요 . <eos>
-----------------------------------------
1
question = <sos> 환자 분 , 지금 부터 전기 를 사용 해 치아 신경 검사 를 해 보 겠 습니다 아프 시 면 손들 어 주 시 겠 어요 ? 
real = 네 알 겠 습니다 . <eos>
predicted= 네 알 겠 습니다 . <eos>
-----------------------------------------
2
question = <sos> 선생 님 , 주기 적 으로 드 시 는 약 있 나요 ?               
real = 영양제 먹 어요 . <eos>
predicted= 영양제 먹 어요 . <eos>
-----------------------------------------
3
question = <sos> 환자 분 , 수술 받 을 때 따로 마취 한 적 있 으실까 요 ?             
real = 아뇨 없 습니다 . <eos>
predicted= 아뇨 없 습니다 . <eos>
-----------------------------------------
4
question = <sos> 선생 님 , 지금 부터 전기 로 치아 신경 검사 를 해 보 곘습니다 아프 면 말씀 해 주 세요 .       
real = 네 알 겠 습니다 . <eos>
predicted= 네 알 겠 습니다 . <eos>
-----------------------------------------
5
question = <sos> 이전 에 치과 에서 무슨 치료 받 으셨 나요 ?                  
real = 삼 일 전 브릿지 받 았 습니다 . <eos>
predicted= 삼 일 전 브릿지 받 았 습니다 . <eos>
---